In [4]:
import sys 
import networkx as nx
import pandas as pd
import numpy as np
import pickle as pic
import random

import cassiopeia.TreeSolver.simulation_tools.simulation_utils as sim_utils
import cassiopeia.TreeSolver.simulation_tools.dataset_generation as data_gen
from cassiopeia.TreeSolver.Node import Node
from cassiopeia.TreeSolver.Cassiopeia_Tree import Cassiopeia_Tree

from tqdm import tqdm_notebook
import matplotlib.pyplot as plt

import subprocess

#import seaborn as sns
import os

In [5]:
#Specify number of cells and the imputation algorithm used
recon_method = "lookahead"
NUM_CELLS = 1500

#Recursive function to travel up the tree and grab a missing character from a node's first ancester
#where it is no longer missing
def get_predecessor_val(tree, node, ind):
    for pred in tree.network.predecessors(node):
#         print(pred.char_vec)
        if pred.char_vec[ind] == '-' or pred.char_vec[ind] == 'H':
            return get_predecessor_val(tree, pred, ind)
        else:
            return pred.char_vec[ind]

In [6]:
# Iterate over the heritable dropout percentages
for recon_method in ["avg", "lookahead", "knn"]:
    print(recon_method)

    for drop in range(6):

        hdropout_percent = str(drop)
        print("Percent: " + hdropout_percent)

        #Establish path
        path = "/data/yosef2/users/richardz/projects/dropout_testing/ground_truth_testing/" + str(NUM_CELLS) + "cells/" + hdropout_percent + "percent"

        #Main loop
        accuracies = []
        for num in range(0, 50):
            #Load the tree, the character matrix, and post-process the tree
            test_recon = pic.load(open(path + "/" + recon_method + "/dropout_cm" + str(num) + "_" + recon_method + ".pkl", 'rb'))
            dropout_cm = pd.read_csv(path + '/dropout_cm' + str(num) + '.txt', sep = '\t', index_col = 0)
            test_ppg = test_recon.post_process(dropout_cm)

            #Create a dictionary to map the names of the nodes to their memory addresses
            names_to_leaves = {}
            for i in list(test_ppg.network.nodes):
                if i.name != "state-node":
                    names_to_leaves[i.name] = i

            #For each named node in the character matrix (post dropout), grab its location in memory and go through
            #its character vector. For each missing value, grab the character from its first non-missing ancestor in 
            #the reconstructed tree. If a character value is still missing at root, implicitly assume its value is 0.
            #Then add the reconstructed row to the list and construct a data frame.
            reconstructed_rows = []
            for index, row in dropout_cm.iterrows():
                node = names_to_leaves[index]
                reconstructed_row = []
                for i in range(len(row)):
                    if row[i] == '-' or row[i] == 'H':
                        char = get_predecessor_val(test_ppg, node, i)
                        if char == None:
                            char = '0'
                        reconstructed_row.append(char)
                    else:
                        reconstructed_row.append(row[i])
                reconstructed_rows.append(reconstructed_row)
            reconstructed_cm = pd.DataFrame(reconstructed_rows)

            #Read in the ground-truth character matrix, before dropout is introduced
            ground_truth_cm = pd.read_csv(path + "/ground_truth_cm" + str(num) + ".txt", sep='\t', index_col = 0)

            #Go through the post-dropout character matrix. For each missing character in the post-dropout character matrix,
            #check to see if the imputed character matrix matches the character in the ground-truth character matrix
            #at that character. If yes, it is considered imputed correctly. Keep a running total of the number of total
            #dropouts and the number of imputed correctly to create a proportion correct.
            num_dropped = 0
            num_correct = 0
            for k in range(dropout_cm.shape[0]):
                for j in range(dropout_cm.shape[1]):
                    if dropout_cm.iloc[k,j] == "-" or dropout_cm.iloc[k,j] == "H":
                        num_dropped += 1
                        if str(ground_truth_cm.iloc[k,j]) == str(reconstructed_cm.iloc[k,j]):
                            num_correct += 1

            accuracy = num_correct/num_dropped
            accuracies.append(accuracy)
            print(num, accuracy)

        #Write the proportions correctly imputed to CSV
        import csv

        with open('/data/yosef2/users/richardz/projects/dropout_testing/ground_truth_testing/' + str(NUM_CELLS) + 'cells/' + recon_method + '_accuracies' + hdropout_percent + '.csv', 'w') as csvFile:
            writer = csv.writer(csvFile)
            writer.writerow(accuracies)
        csvFile.close()

avg
Percent: 0
0 0.9241819632881085
1 0.9390862944162437
2 0.9439551641313051
3 0.91931330472103
4 0.9432314410480349
5 0.9247311827956989
6 0.9258635214827295
7 0.9404567699836868
8 0.9341117597998332
9 0.9376012965964343
10 0.9264836138175376
11 0.9363636363636364
12 0.9478908188585607
13 0.9396694214876034
14 0.9244094488188976
15 0.9377049180327869
16 0.930921052631579
17 0.9357876712328768
18 0.925808997632202
19 0.9070539419087137
20 0.9470198675496688
21 0.9355385920271416
22 0.9285714285714286
23 0.9467905405405406
24 0.9365079365079365
25 0.9302325581395349
26 0.9439799331103679
27 0.9300080450522928
28 0.9381270903010034
29 0.9420654911838791
30 0.9261962692619627
31 0.9263245033112583
32 0.9321608040201005
33 0.9370339685169843
34 0.941830624465355
35 0.9289176090468497
36 0.9193548387096774
37 0.9397794741306191
38 0.9314420803782506
39 0.9414125200642055
40 0.9282051282051282
41 0.9237704918032786
42 0.9206868356500408
43 0.9423076923076923
44 0.9177162048698573
45 0.92139

26 0.7972794506075013
27 0.8202510460251046
28 0.8258240455299977
29 0.8558673469387755
30 0.6717557251908397
31 0.8582325849165228
32 0.8283692126216455
33 0.8107523976766176
34 0.8361100348702053
35 0.8078984156570364
36 0.8432012282890318
37 0.8314672952268709
38 0.846414371962892
39 0.8010121675460321
40 0.7935575144194145
41 0.8719295754650007
42 0.7675943270002676
43 0.8376463784877837
44 0.7612489611777277
45 0.884624468587624
46 0.8404034821058449
47 0.7864960909737029
48 0.8562557801558991
49 0.7806838106370544
Percent: 2
0 0.8179764512595837
1 0.8248830377543249
2 0.7782451528097273
3 0.8070900246551609
4 0.8046839324156827
5 0.8485182632667126
6 0.823242336434345
7 0.8328129242465382
8 0.8001261395562181
9 0.8176923076923077
10 0.7686495035585625
11 0.7852275824475334
12 0.8114937549635406
13 0.8364570976670621
14 0.8212389380530973
15 0.8147440794499619
16 0.7965829439252337
17 0.8462111969635353
18 0.8091280919301435
19 0.7869583993090543
20 0.8040613344384584
21 0.7973462

0 0.7917757842536357
1 0.8069995333644424
2 0.7555477633622201
3 0.8047295240028418
4 0.7334688740439539
5 0.8062952705581593
6 0.8013732833957553
7 0.7953332974079862
8 0.7555101113383322
9 0.791799736990419
10 0.7821743057123505
11 0.8194148125571472
12 0.7929433611884865
13 0.766720533805974
14 0.7611156606772966
15 0.7518833405079638
16 0.7595113943607571
17 0.8052219321148825
18 0.776367881433357
19 0.7165703673132481
20 0.7875213580995425
21 0.7411717264819402
22 0.8080545229244114
23 0.7891673657718121
24 0.8223508459483526
25 0.7927312339077045
26 0.7891216249206582
27 0.7889104548077428
28 0.806417508061532
29 0.7839467337737234
30 0.7803829425586162
31 0.8016429669485011
32 0.8006893867793407
33 0.7364235266187904
34 0.7693219790880672
35 0.7776499286601923
36 0.7957203545392563
37 0.7884421844377351
38 0.7582883755245078
39 0.8013339413977881
40 0.7616535994297933
41 0.8190295639698724
42 0.7441556403953768
43 0.8139915622441912
44 0.7733561402626151
45 0.7758273815511518
46

In [9]:
hdropout_percent = str(2)

path = "/data/yosef2/users/richardz/projects/dropout_testing/ground_truth_testing/" + str(NUM_CELLS) + "cells/" + hdropout_percent + "percent"
accuracies = []

num = 3

test_recon = pic.load(open(path + "/" + recon_method + "/dropout_cm" + str(num) + "_" + recon_method + ".pkl", 'rb'))
dropout_cm = pd.read_csv(path + '/dropout_cm' + str(num) + '.txt', sep = '\t', index_col = 0)
test_ppg = test_recon.post_process(dropout_cm)

names_to_leaves = {}

for i in list(test_ppg.network.nodes):
    if i.name != "state-node":
        names_to_leaves[i.name] = i

reconstructed_rows = []
for index, row in dropout_cm.iterrows():
    print(index)
    node = names_to_leaves[index]
    reconstructed_row = []
    for i in range(len(row)):
        if row[i] == '-':
            char = get_predecessor_val(test_ppg, node, i)
            if char == None:
                char = '0'
            reconstructed_row.append(char)
        else:
            reconstructed_row.append(node.char_vec[i])
    reconstructed_rows.append(reconstructed_row)
reconstructed_cm = pd.DataFrame(reconstructed_rows)

ground_truth_cm = pd.read_csv(path + "/ground_truth_cm" + str(num) + ".txt", sep='\t', index_col = 0)

num_dropped = 0
num_correct = 0
for k in range(10):
    for j in range(10):
        print("new")
        print(dropout_cm.iloc[k,j])
        if dropout_cm.iloc[k,j] == "-":
            num_dropped += 1
            print(ground_truth_cm.iloc[k,j])
            print(reconstructed_cm.iloc[k,j])
            if str(ground_truth_cm.iloc[k,j]) == str(reconstructed_cm.iloc[k,j]):
                num_correct += 1
                print("match")

print(dropout_cm.shape)
print(ground_truth_cm.shape)
print(reconstructed_cm.shape)
accuracy = num_correct/num_dropped
accuracies.append(accuracy)
print(num, accuracy)


c0
['0', '-', '0', '0', '-', '0', '13', '-', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '-', '0', '34', '0', '-', '0', '0', '0', '0', '0', '31', '0', '0', '0', '-', '0']
['0', '-', '0', '0', '-', '0', '13', '-', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '-', '0', '34', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0']
['0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '-', '0', '0', '-', '0', '13', '-', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '-', '0', '34', '0', '-', '0', '0', '0', '0', '0', '31', '0', '0', '0', '-', '0']
['0', '-', '0', '0', '-', '0', '13', '-', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '-', '0', '34', '0', '-', '0', '0', '0', '0', '0', '0', '0', '

['34', '0', '0', '0', '0', '-', '7', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '7', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', 

['0', '0', '0', '0', '28', '0', '0', '0', '0', '0', '0', '-', '0', '11', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '32', '0', '0', '0', '0']
['-', '0', '0', '0', '-', '0', '30', '-', '0', '-', '0', '-', '0', '11', '-', '0', '-', '0', '0', '0', '-', '-', '-', '0', '0', '0', '0', '0', '-', '0', '13', '-', '0', '30', '21', '32', '0', '0', '-', '40']
['0', '0', '0', '0', '-', '0', '30', '-', '0', '0', '0', '-', '0', '11', '-', '0', '-', '0', '0', '0', '-', '-', '-', '0', '0', '0', '0', '0', '-', '0', '13', '0', '0', '30', '21', '32', '0', '0', '-', '40']
['-', '0', '0', '0', '-', '0', '30', '-', '0', '-', '0', '-', '0', '11', '-', '0', '-', '0', '0', '0', '-', '-', '-', '0', '0', '0', '0', '0', '-', '0', '13', '-', '0', '30', '21', '32', '0', '0', '-', '40']
['0', '0', '0', '0', '-', '0', '30', '-', '0', '0', '0', '-', '0', '11', '-', '0', '-', '0', '0', '0', '-', '-', '-', '0', '0', '0', '0', '0', '-', '0', '13', '0', '0', '3

['0', '0', '-', '0', '0', '-', '-', '0', '33', '-', '0', '0', '15', '0', '-', '0', '0', '0', '14', '0', '0', '29', '-', '-', '0', '-', '0', '0', '0', '0', '0', '-', '0', '0', '-', '34', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '7', '0', '33', '0', '0', '0', '15', '0', '0', '0', '0', '0', '14', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '-', '0', '0', '-', '-', '0', '33', '-', '0', '0', '15', '0', '-', '0', '0', '0', '14', '0', '0', '29', '-', '-', '0', '-', '0', '0', '0', '0', '0', '-', '0', '0', '-', '34', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '7', '0', '33', '0', '0', '0', '15', '0', '0', '0', '0', '0', '14', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '7', '0', '33', '0', '0', '0', '15', '0', '0', '0', '0', '0', '0', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0'

['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '-', '-', '-', '0', '0', '24', '-', '0', '15', '0', '0', '0', '0', '0', '-', '-', '0', '38', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '28', '0', '0', '0', '-', '0', '0', '24', '0', '0', '15', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '-', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '-', '-', '-', '0', '0', '24', '-', '0', '15', '0', '0', '0', '0', '0', '-', '-', '0', '38', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '-', '-', '-', '0', '0', '24', '-', '0', '15', '0', '0', '0', '0', '0', '-', '-', '0', '38', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '28', '0', '0', '0', '-', '0', '0', '24', '0', '0', '15', '0', '0', '0', '0', '0', '13',

...

['0', '34', '-', '0', '0', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '-', '-', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '34', '-', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '34', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '21', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '34', '-', '0', '0', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '-', '-', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '34', '-', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0',

['0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '0', '-', '0', '11', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '32', '0', '0', '-', '0']
['0', '0', '0', '0', '28', '0', '0', '0', '0', '0', '0', '-', '0', '11', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '32', '0', '0', '0', '0']
c1394
['0', '0', '-', '0', '0', '-', '7', '0', '33', '0', '0', '20', '15', '0', '0', '0', '0', '0', '0', '0', '0', '-', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '-', '0', '33']
['0', '0', '-', '0', '0', '-', '7', '0', '33', '0', '0', '20', '15', '0', '0', '0', '0', '0', '0', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '13', '0', '0', '-', '0', '33']
['0', '0', '-', '0', '0', '-', '7', '0', '33', '0', '0', '0', '15', '0', '0', '0', '0', '0', '0', '0', '0', '29', '-', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0',

['0', '-', '0', '0', '0', '-', '-', '35', '32', '0', '0', '-', '0', '0', '33', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '38', '-', '-', '0', '0', '-', '34', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '-', '-', '35', '32', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '38', '0', '-', '0', '0', '-', '34', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '-', '0', '0', '0', '-', '-', '35', '32', '0', '0', '-', '0', '0', '33', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '38', '-', '-', '0', '0', '-', '34', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '-', '-', '35', '32', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '38', '0', '-', '0', '0', '-', '34', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '35', '32', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', 

['-', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '-', '-', '0', '0', '-', '0', '0', '0', '-', '0', '0', '-', '0', '0', '-', '-', '0', '-', '0', '-', '0', '-', '0', '-', '0', '-', '0', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '-', '0', '0', '-', '0', '0', '-', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '36', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '36', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '31', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '36', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '

['-', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '28', '0', '-', '0', '-', '0', '0', '-', '0', '0', '0', '0', '37', '0', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '28', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '13', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '33']
['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '-', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', 

In [8]:
def get_predecessor_val(tree, node, ind):
    for pred in tree.network.predecessors(node):
        print(pred.char_vec)
        if pred.char_vec[ind] == '-' or pred.char_vec[ind] == 'H':
            return get_predecessor_val(tree, pred, ind)
        else:
            return pred.char_vec[ind]

In [ ]:
reconstructed_rows = []
for index, row in dropout_cm.iterrows():
    node = names_to_leaves[index]
    reconstructed_row = []
    print(row)
    for i in range(len(row)):
        print(i)
        if row[i] == '-' or row[i] == 'H':
            char = get_predecessor_val(test_ppg, node, i)
            if char == None:
                char = '0'
            reconstructed_row.append(char)
            print(char)
        else:
            reconstructed_row.append(row[i])
    reconstructed_rows.append(reconstructed_row)
    print(reconstructed_row)
reconstructed_cm = pd.DataFrame(reconstructed_rows)
